In [338]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import pickle, os

# 모델 파일 경로
model_filepath = '../data/훈련용/best_model_v1.pkl'

# 모델 불러오기
with open(model_filepath, 'rb') as file:
    classification_model = pickle.load(file)

classification_model

SVC(C=14547.641687966585, cache_size=174673.2578125, class_weight='balanced',
    gamma=0.027760342173282767, max_iter=-1.0, random_state=1, shrinking=False,
    tol=2.6344220036014925e-05)

In [79]:
# 미래 온습도 데이터, 대기질 데이터 호출
future_onssp_DIR = "../data/기온_습도_미세먼지 데이터/미래예측결과"
future_air_DIR = "../data/미래대기질데이터/prophet"
future_traffic_DIR = "../data/교통량 추정 데이터/평균속도예측.csv"
 

[ SO2 | CO | O3 | NO2 | PM10 | PM25 | 지역명 | year | month | day | 도로명 | 기온 | 습도 | 평균속도 | 최고속도 | weekday ]

In [28]:
base_df = pd.read_csv('../data/전처리 완료/dataset.csv')[['지역명', '도로명']].drop_duplicates()
base_df 

지역명      도로명
0      강서구    가로공원로
2      양천구    가로공원로
32     구로구     가마산로
33    영등포구     가마산로
65     금천구  가산디지털1로
...    ...      ...
6619  동대문구      황물로
6641  동대문구      회기로
6663   서초구      효령로
6687   종로구      효자로
6709   동작구    흑석한강로

[359 rows x 2 columns]

In [80]:
pd.read_csv(future_traffic_DIR)

날짜   도로명     평균속도예측
0     2023-06-01  419로  29.583423
1     2023-07-01  419로  29.419581
2     2023-08-01  419로  29.287124
3     2023-09-01  419로  29.395220
4     2023-10-01  419로  29.403783
...          ...   ...        ...
8478  2024-05-31  희우정로  19.101373
8479  2024-06-30  희우정로  19.010959
8480  2024-07-31  희우정로  18.917532
8481  2024-08-31  희우정로  18.824104
8482  2024-09-30  희우정로  18.733691

[8483 rows x 3 columns]

In [138]:
speed = pd.read_csv('../data/교통량 추정 데이터/평균속도.csv')
speed['기준월'] = speed['기준월'].astype('string')
speed = speed[['기준월', '도로명', '평균속도']].groupby(['기준월', '도로명']).mean().reset_index()
speed['year'] = speed['기준월'].str[:4]
speed['month'] = speed['기준월'].str[-2:]
speed.drop('기준월', inplace=True, axis=1)
speed

도로명       평균속도  year month
0        4.19로  29.584000  2023    06
1          가락로  17.449000  2023    06
2        가로공원로  20.669750  2023    06
3     가로공원로76길  15.463000  2023    06
4         가마산로  23.854000  2023    06
...        ...        ...   ...   ...
5613      효창원로  18.584000  2024    04
5614       후암로  18.792500  2024    04
5615       휘경로  21.775000  2024    04
5616       흑석로  16.650133  2024    04
5617      희우정로  19.203000  2024    04

[5618 rows x 4 columns]

In [144]:
future_air_df = pd.DataFrame()
future_onssp_df = pd.DataFrame()
future_traffic_df = pd.read_csv(future_traffic_DIR)

for file in os.listdir(future_air_DIR):
    future_air_df = pd.concat([future_air_df, pd.read_csv(future_air_DIR+"/"+file)]).drop('Unnamed: 0', axis=1)
    
for file in os.listdir(future_onssp_DIR):
    # print(file.split('.')[0])
    temp = pd.read_csv(future_onssp_DIR+"/"+file)
    temp['자치구'] = file.split('.')[0]
    future_onssp_df = pd.concat([future_onssp_df, temp]) 

future_traffic_df.rename(columns={
    '평균속도예측':'평균속도'
}, inplace=True)
future_traffic_df['year'] = future_traffic_df['날짜'].str[:4]
future_traffic_df['month'] = future_traffic_df['날짜'].str[5:7]
future_traffic_df.drop('날짜', inplace=True, axis=1)
future_traffic_df = pd.concat([speed, future_traffic_df])
# future_traffic_df['ds'] = future_traffic_df['year']+future_traffic_df['month']
# future_traffic_df.drop(['year', 'month'], axis=1, inplace=True)

future_traffic_df

도로명       평균속도  year month
0        4.19로  29.584000  2023    06
1          가락로  17.449000  2023    06
2        가로공원로  20.669750  2023    06
3     가로공원로76길  15.463000  2023    06
4         가마산로  23.854000  2023    06
...        ...        ...   ...   ...
8478      희우정로  19.101373  2024    05
8479      희우정로  19.010959  2024    06
8480      희우정로  18.917532  2024    07
8481      희우정로  18.824104  2024    08
8482      희우정로  18.733691  2024    09

[14101 rows x 4 columns]

In [115]:
future_air_df

ds       SO2        CO        O3       NO2       PM10       PM25  \
0    2024-01-01  0.003353  0.754272  0.009072  0.034638  42.876713  33.325194   
1    2024-01-02  0.003384  0.758974  0.008871  0.035694  43.994504  33.966470   
2    2024-01-03  0.003416  0.789326  0.007799  0.037205  48.432514  35.742425   
3    2024-01-04  0.003454  0.799282  0.008909  0.036607  48.813245  36.171086   
4    2024-01-05  0.003480  0.803700  0.010406  0.036688  49.233884  36.871342   
..          ...       ...       ...       ...       ...        ...        ...   
361  2024-12-27  0.001539  0.692627  0.014528  0.027693  29.893032  32.465279   
362  2024-12-28  0.001435  0.715922  0.014859  0.026332  30.590848  33.910649   
363  2024-12-29  0.001346  0.713055  0.017111  0.021604  29.718489  34.095699   
364  2024-12-30  0.001521  0.737580  0.012348  0.027894  30.019763  33.600213   
365  2024-12-31  0.001560  0.741366  0.011690  0.029445  31.161460  34.333490   

     지역명  
0    강남구  
1    강남구  
2    강남구  
3    강남구  
4    강남구  
..   ...  
361  성동구  
362  성동구  
363  성동구  
364  성동구  
365  성동구  

[9150 rows x 8 columns]

In [112]:
maxspd = pd.read_csv('../data/차선정보_전처리/lanes_speed.csv')
maxspd[maxspd['도로명'] == '반포대로']['최고속도'].iloc[0]

50

In [140]:
future_traffic_df[future_traffic_df['도로명']=='반포대로']

도로명       평균속도  year month
174   반포대로  24.539571  2023    06
683   반포대로  24.549143  2023    07
1192  반포대로  24.637571  2023    08
1701  반포대로  23.985000  2023    09
2212  반포대로  25.157286  2023    10
2723  반포대로  23.795857  2023    11
3234  반포대로  24.610429  2023    12
3746  반포대로  25.457286  2024    01
4258  반포대로  25.105571  2024    02
4770  반포대로  25.110714  2024    03
5282  반포대로  24.715714  2024    04
2907  반포대로  24.382708  2023    06
2908  반포대로  24.444291  2023    07
2909  반포대로  24.507928  2023    08
2910  반포대로  24.571564  2023    09
2911  반포대로  24.633148  2023    10
2912  반포대로  24.696785  2023    11
2913  반포대로  24.758855  2023    12
2914  반포대로  24.822995  2024    01
2915  반포대로  24.887135  2024    02
2916  반포대로  24.947137  2024    03
2917  반포대로  25.011277  2024    04
2918  반포대로  25.071279  2024    04
2919  반포대로  25.135418  2024    05
2920  반포대로  25.197489  2024    06
2921  반포대로  25.261629  2024    07
2922  반포대로  25.325769  2024    08
2923  반포대로  25.387840  2024    09

In [351]:
from datetime import datetime, timedelta

# 여기에 예측된 값들도 전송하면 됨. 이후에 예측
def getNewDF(loca, rod):
    # 오늘 날짜
    start_date = datetime.today()

    # 2개월 후 날짜 계산
    end_date = start_date + timedelta(days=60)

    # 날짜 포맷
    date_format = "%Y-%m-%d"

    # 현재 날짜 초기화
    current_date = start_date

    year_col = []
    month_col = []
    day_col = []
    weekday_col = []

    # 반복문을 통해 날짜와 요일 출력
    while current_date <= end_date:
        # YYYY-MM-DD 형식으로 날짜 출력
        date_str = current_date.strftime(date_format) 
        YYYY = date_str[:4]
        MM = date_str[5:7]
        DD = date_str[8:10]
        # 요일 숫자로 출력 (0=월요일, 6=일요일)
        weekday_num = current_date.weekday()

        year_col.append(YYYY)
        month_col.append(MM)
        day_col.append(DD)
        weekday_col.append(weekday_num)

        # print(f"{YYYY}-{MM}-{DD} ({weekday_num})")
        # 다음 날로 이동
        current_date += timedelta(days=1)

    sdate = f'{year_col[0]}-{month_col[0]}-{day_col[0]}'
    edate = f'{year_col[-1]}-{month_col[-1]}-{day_col[-1]}'

    # 미래데이터에서 해당하는 부분 가져오기
    # 예시 코드 : future_onssp_df.iloc[future_onssp_df[future_onssp_df['ds'] == '2023-10-17'].index[0]:future_onssp_df[future_onssp_df['ds'] == '2023-12-17'].index[0]]['기온']

    onssp_begin = future_onssp_df[future_onssp_df['ds'] == sdate].index[0]
    onssp_end = future_onssp_df[future_onssp_df['ds'] == edate].index[0]+1
    future_onssp = future_onssp_df[future_onssp_df['자치구']==loca].iloc[onssp_begin:onssp_end]

    air_begin = future_air_df[future_air_df['ds']==sdate].index[0]
    air_end = future_air_df[future_air_df['ds']==edate].index[0]+1
    future_air = future_air_df[future_air_df['지역명']==loca].iloc[air_begin:air_end]
    
    # temp_future_traffic_df = future_traffic_df[future_traffic_df['도로명']==rod]

    # print('future_air shape:', future_air.shape)
    # print('future_onssp shape:', future_onssp.shape)
    # print('weekday_col len:', len(weekday_col))
    # print(f'y m d col len: {len(year_col)} {len(month_col)} {len(day_col)}')
    maxspeed = None
    try:
        maxspeed = maxspd[maxspd['도로명'] == rod]['최고속도'].iloc[0]
    except:
        maxspeed = 50

    newdf = pd.DataFrame({
        'SO2': future_air['SO2'].values,
        'CO': future_air['CO'].values,
        'O3': future_air['O3'].values,
        'NO2': future_air['NO2'].values,
        'PM10': future_air['PM10'].values,
        'PM25': future_air['PM25'].values,
        '지역명': loca,
        'year': year_col,
        'month': month_col,
        'day': day_col,
        '도로명': rod,
        '기온': future_onssp['기온'].values,
        '습도': future_onssp['상대습도'].values,
        '평균속도': np.nan,
        '최고속도': maxspeed,
        'weekday': weekday_col
    })
    # print(newdf)

    
    # 반복문으로 매핑
    for y in range(int(year_col[0]), int(year_col[-1])+1):
        for m in range(int(month_col[0]), int(month_col[-1])+1):
            y = int(y)
            m = int(m)#.zfill(2)
            # 필터링 조건 설정
            mask = (future_traffic_df['year'] == y) & (future_traffic_df['month'] == m) & (future_traffic_df['도로명'] == rod)
            
            # 조건에 해당하는 데이터 필터링
            filtered_df = future_traffic_df[mask]
            print('maksed:',future_traffic_df[mask])
            # 데이터가 존재하는 경우
            if not filtered_df.empty:
                avg_speed = filtered_df['평균속도'].values[0]
                print(newdf.loc[(newdf['year']==y) & (newdf['month']==m), '평균속도'])
                newdf.loc[(newdf['year']==str(y)) & (newdf['month']==str(m).zfill(2)), '평균속도'] = avg_speed
            else:
                # 데이터가 없는 경우, 기본값으로 설정
                newdf.loc[(newdf['year']==y) & (newdf['month']==m), '평균속도'] = 22.4959188098554
    newdf.fillna(22.4959188098554, inplace=True)



    return newdf

In [294]:
future_traffic_df[(future_traffic_df['year'] == 2024) & (future_traffic_df['month'] == 7) & (future_traffic_df['도로명'] == '반포대로') ]['평균속도'].values[0]

25.261629023699395

In [254]:
str(10).zfill(2)

'10'

In [266]:
future_traffic_df

도로명       평균속도  year  month
0        4.19로  29.584000  2023      6
1          가락로  17.449000  2023      6
2        가로공원로  20.669750  2023      6
3     가로공원로76길  15.463000  2023      6
4         가마산로  23.854000  2023      6
...        ...        ...   ...    ...
8478      희우정로  19.101373  2024      5
8479      희우정로  19.010959  2024      6
8480      희우정로  18.917532  2024      7
8481      희우정로  18.824104  2024      8
8482      희우정로  18.733691  2024      9

[14101 rows x 4 columns]

In [ ]:
# newdf[(newdf['year']==y)&(newdf['month']==m)]['평균속도']

In [192]:
future_air_df[['ds', '지역명']] = future_air_df[['ds', '지역명']].astype('string')
future_air_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9150 entries, 0 to 365
Data columns (total 8 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   ds      9150 non-null   string 
 1   SO2     9150 non-null   float64
 2   CO      9150 non-null   float64
 3   O3      9150 non-null   float64
 4   NO2     9150 non-null   float64
 5   PM10    9150 non-null   float64
 6   PM25    9150 non-null   float64
 7   지역명     9150 non-null   string 
dtypes: float64(6), string(2)
memory usage: 643.4 KB


In [194]:
future_air_df.head()

ds       SO2        CO        O3       NO2       PM10       PM25  \
0  2024-01-01  0.003353  0.754272  0.009072  0.034638  42.876713  33.325194   
1  2024-01-02  0.003384  0.758974  0.008871  0.035694  43.994504  33.966470   
2  2024-01-03  0.003416  0.789326  0.007799  0.037205  48.432514  35.742425   
3  2024-01-04  0.003454  0.799282  0.008909  0.036607  48.813245  36.171086   
4  2024-01-05  0.003480  0.803700  0.010406  0.036688  49.233884  36.871342   

   지역명  
0  강남구  
1  강남구  
2  강남구  
3  강남구  
4  강남구

In [198]:
air_begin = future_air_df[future_air_df['ds']=='2024-01-01'].index[0]
air_end = future_air_df[future_air_df['ds']=='2024-02-11'].index[0]+1
future_air = future_air_df[future_air_df['지역명']=='강남구'].iloc[air_begin:air_end]
future_air

ds       SO2        CO        O3       NO2       PM10       PM25  \
0   2024-01-01  0.003353  0.754272  0.009072  0.034638  42.876713  33.325194   
1   2024-01-02  0.003384  0.758974  0.008871  0.035694  43.994504  33.966470   
2   2024-01-03  0.003416  0.789326  0.007799  0.037205  48.432514  35.742425   
3   2024-01-04  0.003454  0.799282  0.008909  0.036607  48.813245  36.171086   
4   2024-01-05  0.003480  0.803700  0.010406  0.036688  49.233884  36.871342   
5   2024-01-06  0.003439  0.809467  0.011458  0.034671  49.767417  37.353512   
6   2024-01-07  0.003369  0.780697  0.014024  0.029285  47.595785  36.238077   
7   2024-01-08  0.003410  0.796576  0.009985  0.034728  46.598013  34.776905   
8   2024-01-09  0.003413  0.785019  0.010331  0.034988  47.036785  34.343795   
9   2024-01-10  0.003417  0.798798  0.009775  0.035721  50.767681  35.068414   
10  2024-01-11  0.003427  0.792178  0.011360  0.034377  50.425689  34.490000   
11  2024-01-12  0.003427  0.780319  0.013284  0.033763  50.120384  34.247524   
12  2024-01-13  0.003361  0.770408  0.014705  0.031116  49.936789  33.869809   
13  2024-01-14  0.003269  0.726838  0.017579  0.025176  47.068281  31.993825   
14  2024-01-15  0.003289  0.729057  0.013783  0.030154  45.404508  29.885550   
15  2024-01-16  0.003275  0.705209  0.014306  0.030046  45.217770  28.930201   
16  2024-01-17  0.003264  0.708268  0.013858  0.030516  48.372108  29.265924   
17  2024-01-18  0.003263  0.692660  0.015484  0.029019  47.509697  28.437325   
18  2024-01-19  0.003255  0.673669  0.017385  0.028363  46.745943  28.085537   
19  2024-01-20  0.003185  0.658559  0.018725  0.025785  46.170303  27.738321   
20  2024-01-21  0.003091  0.611761  0.021463  0.020022  42.979189  26.028430   
21  2024-01-22  0.003114  0.612712  0.017483  0.025280  41.063916  24.214605   
22  2024-01-23  0.003105  0.589508  0.017782  0.025547  40.697143  23.672021   
23  2024-01-24  0.003102  0.595028  0.017078  0.026476  43.742061  24.526252   
24  2024-01-25  0.003112  0.583569  0.018426  0.025511  42.838897  24.307149   
25  2024-01-26  0.003117  0.570250  0.020035  0.025448  42.100149  24.639289   
26  2024-01-27  0.003062  0.562141  0.021078  0.023506  41.611562  25.032507   
27  2024-01-28  0.002984  0.523456  0.023522  0.018411  38.565182  24.100715   
28  2024-01-29  0.003025  0.533398  0.019261  0.024349  36.847468  23.083376   
29  2024-01-30  0.003034  0.519813  0.019298  0.025294  36.725894  23.336418   
30  2024-01-31  0.003050  0.535331  0.018359  0.026882  40.058280  24.966680   
31  2024-02-01  0.003078  0.533997  0.019504  0.026545  39.479441  25.486226   
32  2024-02-02  0.003100  0.530687  0.020945  0.027060  39.096542  26.503223   
33  2024-02-03  0.003062  0.532243  0.021861  0.025637  38.990168  27.512843   
34  2024-02-04  0.003001  0.502670  0.024220  0.020989  36.347466  27.116407   
35  2024-02-05  0.003054  0.520983  0.019916  0.027293  35.050311  26.543125   
36  2024-02-06  0.003076  0.514874  0.019952  0.028517  35.361942  27.141218   
37  2024-02-07  0.003102  0.536846  0.019053  0.030292  39.136305  29.012490   
38  2024-02-08  0.003138  0.540852  0.020274  0.030045  39.004687  29.666709   
39  2024-02-09  0.003165  0.541714  0.021826  0.030556  39.071048  30.712473   
40  2024-02-10  0.003130  0.546253  0.022880  0.029036  39.413042  31.648032   
41  2024-02-11  0.003068  0.518487  0.025400  0.024202  37.215104  31.080290   

    지역명  
0   강남구  
1   강남구  
2   강남구  
3   강남구  
4   강남구  
5   강남구  
6   강남구  
7   강남구  
8   강남구  
9   강남구  
10  강남구  
11  강남구  
12  강남구  
13  강남구  
14  강남구  
15  강남구  
16  강남구  
17  강남구  
18  강남구  
19  강남구  
20  강남구  
21  강남구  
22  강남구  
23  강남구  
24  강남구  
25  강남구  
26  강남구  
27  강남구  
28  강남구  
29  강남구  
30  강남구  
31  강남구  
32  강남구  
33  강남구  
34  강남구  
35  강남구  
36  강남구  
37  강남구  
38  강남구  
39  강남구  
40  강남구  
41  강남구

In [151]:
future_traffic_df['year']=future_traffic_df['year'].astype('int64')
future_traffic_df['month']=future_traffic_df['month'].astype('int64')

future_traffic_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14101 entries, 0 to 8482
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   도로명     14101 non-null  object 
 1   평균속도    14101 non-null  float64
 2   year    14101 non-null  int64  
 3   month   14101 non-null  int64  
dtypes: float64(1), int64(2), object(1)
memory usage: 550.8+ KB


df를 저 위대로 만든다고 하고 도로별, 지역별로 각각 만들어서 mapping?

In [37]:
predict_dict = dict()

base_df = pd.read_csv('../data/훈련용/X.csv')
locations = ['강남구', '강동구', '강북구', '강서구', '관악구', '광진구', '구로구', '금천구', '노원구',
        '도봉구', '동대문구', '동작구', '마포구', '서대문구', '서초구', '성동구', '성북구', '송파구',
        '양천구', '영등포구', '용산구', '은평구', '종로구', '중구', '중랑구']
roads = ['가로공원로', '가마산로', '가산디지털1로', '가산디지털2로', '가좌로', '강남대로', '강동대로',
        '강서로', '개봉로', '개포로', '개화동로', '거마로', '겸재로', '경인로', '고덕로', '고무래로',
        '고산자로', '고척로', '공릉로', '공원로', '공항대로', '과천대로', '관악로', '광나루로', '광평로',
        '구로동로', '구로중앙로', '구의강변로', '국제금융로', '국회대로', '금낭화로', '금오로', '금하로',
        '긴고랑로', '낙성대로', '난계로', '난곡로', '남대문로', '남부순환로', '노량진로', '노원로',
        '노해로', '녹사평대로', '논현로', '능동로', '다산로', '답십리로', '당산로', '대림로', '대방천로',
        '대학로', '대흥로', '덕릉로', '도곡로', '도당로', '도림로', '도봉로', '도산대로', '도신로',
        '도영로', '독막로', '독산로', '독서당로', '돌곶이로', '동교로', '동남로', '동소문로', '동일로',
        '동작대로', '동호로', '등촌로', '디지털로', '뚝섬로', '마곡중앙5로', '마곡중앙로', '마들로',
        '마장로', '마천로', '마포대로', '만리재로', '망우로', '매헌로', '면목천로', '명달로', '모래내로',
        '목동남로', '목동동로', '목동로', '목동로3길', '목동서로', '목동중앙로', '무학로', '문래로',
        '문성로', '문정로', '바우뫼로', '반포대로', '밤고개로', '밤고개로21길', '방배로', '방학로',
        '방화대로', '백련산로', '백범로', '백제고분로', '버드나루로', '범안로', '벚꽃로', '보국문로',
        '보문로', '봉우재로', '봉은사로', '봉천로', '봉화산로', '부일로', '북한산로', '사가정로', '사당로',
        '사임당로', '사직로', '사평대로', '살곶이길', '삼성로', '삼양로', '삼일대로', '삼전로', '삼학사로',
        '상계로', '상도로', '상봉로', '상일로', '새말로', '새문안로', '새창로', '서강로', '서빙고로',
        '서소문로', '서오릉로', '서운로', '서울시립대로', '서초대로', '서초중앙로', '서해안로', '석촌호수로',
        '선릉로', '선유로', '섬밭로', '성내로', '성북로', '성산로', '성암로', '성현로', '세검정로',
        '세종대로', '소월로', '솔샘로', '송이로', '송파대로', '수락산로', '수명로', '수색로', '숙선옹주로',
        '시흥대로', '신길로', '신내로', '신내역로', '신도림로', '신림로', '신목로', '신반포로', '신사로',
        '신월로', '신정로', '신정로7길', '신정이펜1로', '신촌로', '신풍로', '쑥고개로', '아리랑로',
        '아차산로', '안암로', '안양천로', '압구정로', '양녕로', '양재대로', '양천로', '양평로', '양화로',
        '언주로', '여의공원로', '여의나루로', '여의대방로', '여의동로', '여의서로', '역삼로', '연남로',
        '연서로', '연희로', '영동대로', '영등포로', '영신로', '영중로', '오금로', '오리로', '오목로',
        '오패산로', '올림픽로', '올림픽로35길', '와우산로', '왕산로', '왕십리로', '용마산로', '원효로',
        '월계로', '월드컵로', '월드컵북로', '위례성대로', '율곡로', '은천로', '은평로', '은행나무로',
        '을지로', '응암로', '의사당대로', '이문로', '이촌로', '이태원로', '인수봉로', '인촌로', '일원로',
        '자곡로', '자양로', '자하문로', '잔다리로', '잠실로', '잠원로', '장승배기로', '장안벚꽃로',
        '장충단로', '장한로', '전농로', '정릉로', '제기로', '종로', '종암로', '중계로', '중대로',
        '중랑천로', '중앙로', '증산로', '지봉로', '진관1로', '진흥로', '창경궁로', '창의문로', '창전로',
        '천왕로', '천중로', '천호대로', '청계천로', '청파로', '초안산로', '초원로', '충민로', '태봉로',
        '테헤란로', '토정로', '통일로', '퇴계로', '평창문화로', '풍산로', '하늘길', '학동로', '한강대로',
        '한글비석로', '한남대로', '한천로', '한천로58길', '해등로', '행당로', '허준로', '헌릉로',
        '현충로', '호암로', '홍릉로', '화곡로', '화랑로', '황물로', '회기로', '효령로', '효자로',
        '흑석한강로']


# 이 딕셔너리들 나중에 인코딩에 써먹음.
location_dict = dict()
location_encoding = dict()
road_dict = dict()
road_encoding = dict()

for loc in range(len(locations)):
    location_dict[locations[loc]] = dict()
    location_encoding[locations[loc]] = loc
for road in range(len(roads)):
    road_dict[roads[road]] = dict()
    road_encoding[roads[road]] = road
 

In [48]:
base_df = pd.read_csv('../data/전처리 완료/dataset.csv')[['지역명', '도로명']].drop_duplicates()
base_df 

지역명      도로명
0      강서구    가로공원로
2      양천구    가로공원로
32     구로구     가마산로
33    영등포구     가마산로
65     금천구  가산디지털1로
...    ...      ...
6619  동대문구      황물로
6641  동대문구      회기로
6663   서초구      효령로
6687   종로구      효자로
6709   동작구    흑석한강로

[359 rows x 2 columns]

In [49]:
base_df[base_df['지역명'] == '강남구']

지역명      도로명
210   강남구      개포로
544   강남구      광평로
840   강남구    남부순환로
1094  강남구      논현로
1362  강남구      도곡로
1450  강남구     도산대로
2409  강남구     밤고개로
2431  강남구  밤고개로21길
2715  강남구     봉은사로
2930  강남구      삼성로
3399  강남구      선릉로
4157  강남구     압구정로
4322  강남구      언주로
4476  강남구      역삼로
4535  강남구     영동대로
5163  강남구      일원로
5185  강남구      자곡로
5991  강남구     테헤란로
6218  강남구      학동로
6439  강남구      헌릉로

In [352]:
for loc in locations:
    roads_series = base_df[base_df['지역명'] == loc]['도로명']
    for rs in roads_series:
        # print(loc, rs)
        location_dict[loc][rs] = getNewDF(loc, rs)

location_dict['서초구']

maksed:      도로명      평균속도  year  month
387  개포로  20.63748  2024      6
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
388  개포로  20.662958  2024      7
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
389  개포로  20.688436  2024      8
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명      평균속도  year  month
387  개포로  20.63748  2024      6
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
388  개포로  20.662958  2024      7
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
389  개포로  20.688436  2024      8
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명      평균속도  year  month
387  개포로  20.63748  2024      6
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
388  개포로  20.662958  2024      7
Series([], Name: 평균속도, dtype: float64)
maksed:      도로명       평균속도  year  month
389  개포로  20.688436  2024      8
Series([], Name: 평균속도, dtype

{'강남대로':          SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
 0   0.001896  0.329975  0.041209  0.017206  28.295143  17.055322  서초구  2024   
 1   0.001866  0.326985  0.040382  0.017903  27.174611  16.772764  서초구  2024   
 2   0.001870  0.348499  0.039225  0.018825  30.849987  18.195477  서초구  2024   
 3   0.001863  0.342549  0.039826  0.018251  29.180134  17.801273  서초구  2024   
 4   0.001890  0.344218  0.040216  0.018542  27.422406  18.016270  서초구  2024   
 ..       ...       ...       ...       ...        ...        ...  ...   ...   
 56  0.001690  0.329656  0.029738  0.012820  12.322624  10.351559  서초구  2024   
 57  0.001677  0.329441  0.029286  0.013551  12.615257  10.470767  서초구  2024   
 58  0.001696  0.354825  0.028568  0.014541  17.765390  12.342857  서초구  2024   
 59  0.001703  0.353767  0.029662  0.014069  17.597131  12.431818  서초구  2024   
 60  0.001743  0.361243  0.030591  0.014494  17.332464  13.148931  서초구  2024   
 
    month day   도로명         기온

# NEWDF 모두 완료되면 분류기 돌려서 DF에 합쳐라

0   SO2      6715 non-null   float64 <br>
 1   CO       6715 non-null   float64 <br>
 2   O3       6715 non-null   float64 <br>
 3   NO2      6715 non-null   float64 <br>
 4   PM10     6715 non-null   float64 <br>
 5   PM25     6715 non-null   float64 <br>
 6   지역명      6715 non-null   int64 <br>  
 7   month    6715 non-null   int64 <br>  
 8   day      6715 non-null   int64 <br>  
 9   도로명      6715 non-null   int64 <br>  
 10  기온       6715 non-null   float64 <br>
 11  습도       6715 non-null   float64 <br>
 12  오염범례     6715 non-null   int64  <br> 
 13  평균속도     6715 non-null   float64 <br>
 14  최고속도     6715 non-null   float64 <br>
 15  weekday  6715 non-null   int64  <br>

In [337]:
from sklearn.preprocessing import LabelEncoder, StandardScaler

with open('../data/훈련용/scaler.pkl', 'rb') as f:
    scaler_loaded = pickle.load(f)
location_encoder = LabelEncoder()
road_encoder = LabelEncoder()

location_encoder.fit(list(location_encoding.keys()))
road_encoder.fit(list(road_encoding.keys()))


LabelEncoder()

In [311]:
location_dict['서초구']['서초대로'].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 61 entries, 0 to 60
Data columns (total 16 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   SO2      61 non-null     float64
 1   CO       61 non-null     float64
 2   O3       61 non-null     float64
 3   NO2      61 non-null     float64
 4   PM10     61 non-null     float64
 5   PM25     61 non-null     float64
 6   지역명      61 non-null     int64  
 7   year     61 non-null     object 
 8   month    61 non-null     object 
 9   day      61 non-null     object 
 10  도로명      61 non-null     int64  
 11  기온       61 non-null     float64
 12  습도       61 non-null     float64
 13  평균속도     61 non-null     float64
 14  최고속도     61 non-null     float64
 15  weekday  61 non-null     int64  
dtypes: float64(10), int64(3), object(3)
memory usage: 7.8+ KB


In [312]:
test_df = location_dict['서초구']['반포대로']
test_df['year'] = test_df['year'].astype('int64')
test_df['month'] = test_df['month'].astype('int64')
test_df['day'] = test_df['day'].astype('int64')

In [342]:
from sklearn.preprocessing import StandardScaler


# test_df['최고속도'] = test_df['최고속도'].astype('float64')
# test_df['지역명'] = location_encoder.transform(test_df['지역명'])
# test_df['도로명'] = road_encoder.transform(test_df['도로명'])

def scale_float64_columns(df):
    # float64 타입의 열만 선택
    float64_cols = df.select_dtypes(include=['float64']).columns
    print(df.info())
    # StandardScaler를 초기화
    scaler = scaler_loaded

    # float64 타입의 열에 대해서만 스케일링 적용
    df[float64_cols] = scaler.transform(df[float64_cols])

    return df

test_df = scale_float64_columns(test_df)

test_df

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 61 entries, 0 to 60
Data columns (total 16 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   SO2      61 non-null     float64
 1   CO       61 non-null     float64
 2   O3       61 non-null     float64
 3   NO2      61 non-null     float64
 4   PM10     61 non-null     float64
 5   PM25     61 non-null     float64
 6   지역명      61 non-null     int64  
 7   year     61 non-null     int64  
 8   month    61 non-null     int64  
 9   day      61 non-null     int64  
 10  도로명      61 non-null     int64  
 11  기온       61 non-null     float64
 12  습도       61 non-null     float64
 13  평균속도     61 non-null     float64
 14  최고속도     61 non-null     float64
 15  weekday  61 non-null     int64  
dtypes: float64(10), int64(6)
memory usage: 7.8 KB
None


SO2          CO             O3           NO2      PM10      PM25  \
0   2.777488e+09 -464.582809  407431.200065 -8.177859e+05 -1.478019 -1.572155   
1   4.471378e+09 -356.250054  225321.585763  3.725861e+05 -1.478025 -1.572516   
2   3.631088e+09 -383.822865  192246.909615  5.030838e+05 -1.478039 -1.572577   
3   3.731735e+09 -185.419042  145957.841874  6.755325e+05 -1.477995 -1.572267   
4   3.537057e+09 -240.291310  170011.401509  5.681824e+05 -1.478015 -1.572353   
..           ...         ...            ...           ...       ...       ...   
56 -3.598445e+09 -482.629562  -63670.780383 -1.638825e+06 -1.478225 -1.573693   
57 -1.371144e+09 -359.191362 -233622.275511 -4.484202e+05 -1.478215 -1.573979   
58 -1.721646e+09 -361.173364 -251709.180333 -3.115943e+05 -1.478212 -1.573953   
59 -1.178931e+09 -127.072818 -280466.685268 -1.264193e+05 -1.478150 -1.573544   
60 -9.813308e+08 -136.831287 -236677.208002 -2.147259e+05 -1.478152 -1.573525   

    지역명  year  month  day  도로명        기온        습도      평균속도       최고속도  \
0    14  2024      6    2   96 -2.832929 -3.233989 -8.254208 -10.191411   
1    14  2024      6    3   96 -2.832643 -3.233969 -8.254208 -10.191411   
2    14  2024      6    4   96 -2.832865 -3.233970 -8.254208 -10.191411   
3    14  2024      6    5   96 -2.833010 -3.233931 -8.254208 -10.191411   
4    14  2024      6    6   96 -2.832837 -3.233910 -8.254208 -10.191411   
..  ...   ...    ...  ...  ...       ...       ...       ...        ...   
56   14  2024      7   28   96 -2.828881 -3.233659 -8.219127 -10.191411   
57   14  2024      7   29   96 -2.828539 -3.233651 -8.219127 -10.191411   
58   14  2024      7   30   96 -2.828704 -3.233665 -8.219127 -10.191411   
59   14  2024      7   31   96 -2.828802 -3.233637 -8.219127 -10.191411   
60   14  2024      8    1   96 -2.828596 -3.233626 -8.184045 -10.191411   

    weekday  
0         6  
1         0  
2         1  
3         2  
4         3  
..      ...  
56        6  
57        0  
58        1  
59        2  
60        3  

[61 rows x 16 columns]

In [319]:
predict_df = test_df.drop('year', axis=1).copy()
predict_df

SO2         CO          O3         NO2      PM10      PM25  지역명  \
0   1612.085850 -10.441511  151.606052 -121.893579 -1.355530 -1.333411   14   
1   2595.237199  -7.886750   83.859291   55.569717 -1.359762 -1.391023   14   
2   2107.523883  -8.536987   71.555151   75.024615 -1.368912 -1.400870   14   
3   2165.940627  -3.858123   54.335113  100.733652 -1.338901 -1.351289   14   
4   2052.947208  -5.152150   63.283299   84.729649 -1.352536 -1.365027   14   
..          ...        ...         ...         ...       ...       ...  ...   
56 -2088.571667 -10.867099  -23.649019 -244.295981 -1.496720 -1.578943   14   
57  -795.823178  -7.956114  -86.872828  -66.827717 -1.490187 -1.624645   14   
58  -999.258027  -8.002854  -93.601354  -46.429408 -1.487797 -1.620490   14   
59  -684.260508  -2.482171 -104.299459  -18.823101 -1.445744 -1.555249   14   
60  -569.571585  -2.712300  -88.009296  -31.988060 -1.447117 -1.552149   14   

    month  day  도로명        기온        습도      평균속도      최고속도  weekday  
0       6    2   96 -2.723255 -3.179368 -6.438337 -8.423231        6  
1       6    3   96 -2.700740 -3.171682 -6.438337 -8.423231        0  
2       6    4   96 -2.718213 -3.172254 -6.438337 -8.423231        1  
3       6    5   96 -2.729678 -3.158005 -6.438337 -8.423231        2  
4       6    6   96 -2.716055 -3.150221 -6.438337 -8.423231        3  
..    ...  ...  ...       ...       ...       ...       ...      ...  
56      7   28   96 -2.403723 -3.057814 -5.938607 -8.423231        6  
57      7   29   96 -2.376694 -3.055097 -5.938607 -8.423231        0  
58      7   30   96 -2.389773 -3.060133 -5.938607 -8.423231        1  
59      7   31   96 -2.397466 -3.049870 -5.938607 -8.423231        2  
60      8    1   96 -2.381203 -3.045636 -5.438876 -8.423231        3  

[61 rows x 15 columns]

In [328]:
classification_model.predict(predict_df)

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


array([4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4.,
       4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4.,
       4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4., 4.,
       4., 4., 4., 4., 4., 4., 4., 4., 4., 4.])

In [353]:
for goos in location_dict.keys():
    for ros in location_dict[goos].keys():
        ros_df = None
        ros_df = location_dict[goos][ros]
        print(ros_df)
        try:
            ros_df['지역명'] = location_encoder.transform(ros_df['지역명'])
            ros_df['도로명'] = road_encoder.transform(ros_df['도로명'])
        except:
            pass
        ros_df['year'] = ros_df['year'].astype('int64')
        ros_df['지역명'] = ros_df['지역명'].astype('int64')
        ros_df['month'] = ros_df['month'].astype('int64')
        ros_df['day'] = ros_df['day'].astype('int64')
        ros_df['최고속도'] = ros_df['최고속도'].astype('float64')
        # print(ros_df.drop('year', axis=1).columns)
        ros_predict = scale_float64_columns(ros_df.drop('year', axis=1)).copy() 
        prediction = classification_model.predict(ros_predict)
        ros_df['예측 오염범례'] = prediction
        ros_df['청소유무'] = (ros_df['예측 오염범례'] > 3)


         SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002397  0.394227  0.043772  0.014152  23.441079  17.454079  강남구  2024   
1   0.002384  0.384642  0.043162  0.014789  22.594750  17.097129  강남구  2024   
2   0.002378  0.401957  0.041564  0.015984  25.124180  18.016777  강남구  2024   
3   0.002381  0.400369  0.042040  0.015178  23.682902  17.744108  강남구  2024   
4   0.002378  0.394962  0.042802  0.015166  22.397569  17.908130  강남구  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.002300  0.302992  0.029164  0.011431  10.788312  14.415910  강남구  2024   
57  0.002322  0.292409  0.028973  0.012098  11.255184  14.417664  강남구  2024   
58  0.002348  0.310578  0.027881  0.013349  15.155076  15.717018  강남구  2024   
59  0.002381  0.311608  0.028943  0.012623  15.107582  15.832557  강남구  2024   
60  0.002406  0.310445  0.030362  0.012710  15.204810  16.380282  강남구  2024   

   month day  도로명         기온         습도       평균속도 

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framewor

         SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002397  0.394227  0.043772  0.014152  23.441079  17.454079  강남구  2024   
1   0.002384  0.384642  0.043162  0.014789  22.594750  17.097129  강남구  2024   
2   0.002378  0.401957  0.041564  0.015984  25.124180  18.016777  강남구  2024   
3   0.002381  0.400369  0.042040  0.015178  23.682902  17.744108  강남구  2024   
4   0.002378  0.394962  0.042802  0.015166  22.397569  17.908130  강남구  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.002300  0.302992  0.029164  0.011431  10.788312  14.415910  강남구  2024   
57  0.002322  0.292409  0.028973  0.012098  11.255184  14.417664  강남구  2024   
58  0.002348  0.310578  0.027881  0.013349  15.155076  15.717018  강남구  2024   
59  0.002381  0.311608  0.028943  0.012623  15.107582  15.832557  강남구  2024   
60  0.002406  0.310445  0.030362  0.012710  15.204810  16.380282  강남구  2024   

   month day   도로명         기온         습도       평균속도

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framewor

         SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002397  0.394227  0.043772  0.014152  23.441079  17.454079  강남구  2024   
1   0.002384  0.384642  0.043162  0.014789  22.594750  17.097129  강남구  2024   
2   0.002378  0.401957  0.041564  0.015984  25.124180  18.016777  강남구  2024   
3   0.002381  0.400369  0.042040  0.015178  23.682902  17.744108  강남구  2024   
4   0.002378  0.394962  0.042802  0.015166  22.397569  17.908130  강남구  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.002300  0.302992  0.029164  0.011431  10.788312  14.415910  강남구  2024   
57  0.002322  0.292409  0.028973  0.012098  11.255184  14.417664  강남구  2024   
58  0.002348  0.310578  0.027881  0.013349  15.155076  15.717018  강남구  2024   
59  0.002381  0.311608  0.028943  0.012623  15.107582  15.832557  강남구  2024   
60  0.002406  0.310445  0.030362  0.012710  15.204810  16.380282  강남구  2024   

   month day  도로명         기온         습도       평균속도 

...

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


         SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002188  0.354080  0.043789  0.014034  18.458979  14.035491  중랑구  2024   
1   0.002153  0.344124  0.042811  0.014661  17.696731  13.449019  중랑구  2024   
2   0.002135  0.355341  0.042054  0.015100  18.822520  13.658176  중랑구  2024   
3   0.002135  0.356126  0.042544  0.014374  18.127660  13.865846  중랑구  2024   
4   0.002124  0.350343  0.043257  0.013919  16.976335  14.122493  중랑구  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.001972  0.282032  0.029267  0.011067  10.552296  14.317289  중랑구  2024   
57  0.001965  0.273037  0.028444  0.011797  11.103571  14.075469  중랑구  2024   
58  0.001974  0.286303  0.027935  0.012349  13.553137  14.621507  중랑구  2024   
59  0.002001  0.290148  0.028765  0.011736  14.158122  15.146303  중랑구  2024   
60  0.002016  0.288339  0.029905  0.011387  14.249092  15.688467  중랑구  2024   

   month day  도로명         기온         습도       평균속도 

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


         SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002188  0.354080  0.043789  0.014034  18.458979  14.035491  중랑구  2024   
1   0.002153  0.344124  0.042811  0.014661  17.696731  13.449019  중랑구  2024   
2   0.002135  0.355341  0.042054  0.015100  18.822520  13.658176  중랑구  2024   
3   0.002135  0.356126  0.042544  0.014374  18.127660  13.865846  중랑구  2024   
4   0.002124  0.350343  0.043257  0.013919  16.976335  14.122493  중랑구  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.001972  0.282032  0.029267  0.011067  10.552296  14.317289  중랑구  2024   
57  0.001965  0.273037  0.028444  0.011797  11.103571  14.075469  중랑구  2024   
58  0.001974  0.286303  0.027935  0.012349  13.553137  14.621507  중랑구  2024   
59  0.002001  0.290148  0.028765  0.011736  14.158122  15.146303  중랑구  2024   
60  0.002016  0.288339  0.029905  0.011387  14.249092  15.688467  중랑구  2024   

   month day  도로명         기온         습도       평균속도 

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:443: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(
/Library/Frameworks/Python.framewor

In [365]:
seocho_roads = location_dict['서초구'].keys()

for goo_name in location_dict.keys():
    print(f'<----------{goo_name}---------->')
    for road in location_dict[goo_name].keys():
        plan = ""
        seocho_road_df = location_dict[goo_name][road]
        result = seocho_road_df['예측 오염범례']
        print(f'{road}:{result.unique()}')
        for r in result.values:
            if r > 3:
                plan += "X"
            else:
                plan += "-"
        print(plan)

<----------강남구---------->
개포로:[4. 3. 0.]
XXXXXXX--XXXXXXXXXXXX-----XXXXXXXXX--XXXXXXXXXXXXX----XXXXXXX
광평로:[4.]
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
남부순환로:[4. 0.]
XXXXXXXXXX--XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
논현로:[4. 2.]
XXXXXXXXXXXX-XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
도곡로:[4. 3.]
XXXXXXXXXXXXXXXXXXXXXX----XXXXXXXXXXXXXXXXXXXXXXXXXX--XXXXXXX
도산대로:[4. 3.]
XXXXXXXXXX---X--XXXXXXXXXXXXXXXXXXXXXXXXXX--XXXXXXXXXXXXXXXXX
밤고개로:[4.]
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
밤고개로21길:[4. 3.]
XXXXXXX---XXXXXXXXXXXXXXXXXXXXXXXXX--XXXXXXXXXXXXXXXXXXXXXXXX
봉은사로:[4.]
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
삼성로:[4.]
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
선릉로:[4. 2.]
XXXXXXXXXXXXXX---XXXXXXXXXXXXXXXXXXXXXXXXX---XXXXXXXXXXXXXXXX
압구정로:[4. 3.]
XX---XXXXXXXXXXXXXXXXXXXXXXXXX---XX---XXXXXXXXXXXXXXXXXXXXXX-
언주로:[4.]
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
역삼로:[4. 3.]
XX

성능이 개같은건 미래예측변수가 개같은 것이라고 결론지음

# 시각화

한 번 청소를 하면 향후 6일 간의 청소유무를 False로 설정 <br>
각 도로별 청소여부를 df[청소여부].values의 배열로 받은 후 최적화 계산. - O(N^2) <br>
그렇게 나온 결과를 하나의 dataframe으로 concat 후 시간대별로 시각화

In [374]:
def scheduleOptimize(values):
    # values는 list이다. 
    for v_idx in range(len(values)):
        if values[v_idx] == 'X':
            for i in range(v_idx+1, v_idx+7):
                if i >= len(values):
                    return values
                values[i] = '-'
            v_idx += 7
    return values

before = "XXXXX-XXXX----X-XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX"
after = ""
for element in scheduleOptimize(list(before)):
    after += element
print("before:", before)
print("after:", after)

before: XXXXX-XXXX----X-XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
after: X------X------X------X------X------X------X------X------X----


In [381]:
def scheduleOptimizeReal(values):
    # values는 list이다. 
    for v_idx in range(len(values)):
        if values[v_idx]:
            for i in range(v_idx+1, v_idx+7):
                if i >= len(values):
                    return values
                values[i] = False
            v_idx += 7
    return values

In [385]:
for goo_name in location_dict.keys():
    # print(f'<----------{goo_name}---------->')
    for road in location_dict[goo_name].keys():
        # print(f'<{road}>')
        # plan = ""
        target_road_df = location_dict[goo_name][road]
        clean_list = list(target_road_df['청소유무'].values)
        # print(clean_list)
        location_dict[goo_name][road]['청소일정'] = scheduleOptimizeReal(clean_list)


In [389]:
import pickle, json

with open('../data/결과 딕셔너리/청소일정df.pkl', 'wb') as pickle_file:
    pickle.dump(location_dict, pickle_file)

# 아 이런 형식은 json 말고 pickle로만 저장되는구나.
# with open('../data/결과 딕셔너리/청소일정df.json', 'w', encoding='utf-8') as json_file:
#     json.dump(location_dict, json_file, ensure_ascii=False, indent=4)

# Pickle 파일에서 불러오기
with open('../data/결과 딕셔너리/청소일정df.pkl', 'rb') as pickle_file:
    saved_data = pickle.load(pickle_file)

print(saved_data)


{'강남구': {'개포로':          SO2        CO        O3       NO2       PM10       PM25  지역명  year  \
0   0.002397  0.394227  0.043772  0.014152  23.441079  17.454079    0  2024   
1   0.002384  0.384642  0.043162  0.014789  22.594750  17.097129    0  2024   
2   0.002378  0.401957  0.041564  0.015984  25.124180  18.016777    0  2024   
3   0.002381  0.400369  0.042040  0.015178  23.682902  17.744108    0  2024   
4   0.002378  0.394962  0.042802  0.015166  22.397569  17.908130    0  2024   
..       ...       ...       ...       ...        ...        ...  ...   ...   
56  0.002300  0.302992  0.029164  0.011431  10.788312  14.415910    0  2024   
57  0.002322  0.292409  0.028973  0.012098  11.255184  14.417664    0  2024   
58  0.002348  0.310578  0.027881  0.013349  15.155076  15.717018    0  2024   
59  0.002381  0.311608  0.028943  0.012623  15.107582  15.832557    0  2024   
60  0.002406  0.310445  0.030362  0.012710  15.204810  16.380282    0  2024   

    month  day  도로명         기온     